In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
#!pip install --upgrade scenedetect[opencv]
#!pip install opencv-python --upgrade
!apt-get install -y ffmpeg
!pip install llama-index
!pip install llama-index-llms-huggingface


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
0 upgraded, 0 newly installed, 0 to remove and 45 not upgraded.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.4/15.4 MB 49.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 61.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 8.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 141.9/141.9 kB 16.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.7/320.7 kB 31.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 57.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 290.4/290.4 kB 24.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 

In [ ]:
videopath = "/content/drive/MyDrive/Test video/NYPD_N_00000592.mp4"
output_path = "/content/clips"

!scenedetect -i "$videopath" -o "$output_path" detect-adaptive list-scenes

metadata = {
    'name': os.path.basename(videopath),
    'path': videopath,
    'total_scenes': len(scenes)
}

[PySceneDetect] PySceneDetect 0.6.3
[PySceneDetect] Output directory set:
  /content/clips
[PySceneDetect] Scene list filename format:
  $VIDEO_NAME-Scenes.csv
[PySceneDetect] Downscale factor set to 5, effective resolution: 256 x 144
[PySceneDetect] Detecting scenes...
  Detected: 58 | Progress: 100% 26420/26433 [02:38<00:00, 166.54frames/s]
[PySceneDetect] Processed 26420 frames in 158.6 seconds (average 166.54 FPS).
[PySceneDetect] Detected 59 scenes, average shot length 8.1 seconds.
[PySceneDetect] Writing scene list to CSV file:
  /content/clips/NYPD_N_00000592-Scenes.csv
[PySceneDetect] Scene List:
-----------------------------------------------------------------------
 | Scene # | Start Frame |  Start Time  |  End Frame  |   End Time   |
-----------------------------------------------------------------------
 |      1  |           1 | 00:00:00.000 |         450 | 00:00:08.172 |
 |      2  |         451 | 00:00:08.172 |        1080 | 00:00:19.614 |
 |      3  |        1081 | 00:0

In [ ]:
scenedetect.video_splitter.VideoMetadata(name, path, total_scenes)

In [ ]:
videopath = "/content/drive/MyDrive/Test video/NYPD_N_00000592.mp4"
output_path = "/content/clips"
!scenedetect -i "$videopath" -o "$output_path" detect-adaptive split-video

In [ ]:
videopath = "/content/drive/MyDrive/Test video/NYPD_N_00000592.mp4"
output_path = "/content/clips"
!scenedetect -i "$videopath" -o "$output_path" detect-adaptive split-video

[PySceneDetect] PySceneDetect 0.6.3
[PySceneDetect] Output directory set:
  /content/clips
[PySceneDetect] ffmpeg arguments: -map 0 -c:v libx264 -preset veryfast -crf 22 -c:a aac
[PySceneDetect] Downscale factor set to 5, effective resolution: 256 x 144
[PySceneDetect] Detecting scenes...
  Detected: 58 | Progress: 100% 26420/26433 [02:39<00:00, 165.95frames/s]
[PySceneDetect] Processed 26420 frames in 159.3 seconds (average 165.90 FPS).
[PySceneDetect] Detected 59 scenes, average shot length 8.1 seconds.
[PySceneDetect] Splitting input video using ffmpeg, output path template:
  $VIDEO_NAME-Scene-$SCENE_NUMBER.mp4
  0% 0/26420 [00:00<?, ?frame/s]ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-g

In [ ]:
import os
import pandas as pd
from scenedetect import VideoManager, SceneManager
from scenedetect.detectors import ContentDetector

# Function to detect scenes and return timestamps
def detect_scenes(video_path):
    video_manager = VideoManager([video_path])
    scene_manager = SceneManager()
    scene_manager.add_detector(ContentDetector())

    video_manager.set_downscale_factor()
    video_manager.start()

    scene_manager.detect_scenes(frame_source=video_manager)

    scene_list = scene_manager.get_scene_list()

    video_manager.release()

    # Extracting start and end times of each scene
    scene_timestamps = [(scene[0].get_timecode(), scene[1].get_timecode()) for scene in scene_list]

    return scene_timestamps

# Path to the video file
video_path = '/content/drive/MyDrive/Test video/NYPD_N_00000592.mp4'  # Change to your video path

# Detect scenes and get timestamps
scene_timestamps = detect_scenes(video_path)

# Convert timestamps to DataFrame
df_scenes = pd.DataFrame(scene_timestamps, columns=['Start Time', 'End Time'])

# Save to CSV
#csv_output_path = '/content/scene_timestamps.csv'
#df_scenes.to_csv(csv_output_path, index=False)

print(df_scenes)


ERROR:pyscenedetect:VideoManager is deprecated and will be removed.
INFO:pyscenedetect:Loaded 1 video, framerate: 55.063 FPS, resolution: 1280 x 720
INFO:pyscenedetect:Downscale factor set to 5, effective resolution: 256 x 144
INFO:pyscenedetect:Detecting scenes...


       Start Time      End Time
0    00:00:00.000  00:00:07.192
1    00:00:07.192  00:00:07.464
2    00:00:07.464  00:00:15.310
3    00:00:15.310  00:00:15.582
4    00:00:15.582  00:00:15.855
..            ...           ...
149  00:07:00.881  00:07:01.154
150  00:07:01.154  00:07:01.426
151  00:07:01.426  00:07:33.172
152  00:07:33.172  00:07:50.624
153  00:07:50.624  00:07:59.814

[154 rows x 2 columns]


In [ ]:
import os
from IPython.display import HTML
from base64 import b64encode

video_folder_path = '/content/clips'  # Change to your folder path
video_files = [f for f in os.listdir(video_folder_path) if f.endswith(('.mp4', '.avi', '.mov', '.mkv'))]
#video_files.sort()  # Optional: sort the video files
#print(video_files)

def display_video(video_path):
    mp4 = open(video_path,'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
    video_html = f"""
    <video width="640" height="480" controls>
        <source src="{data_url}" type="video/mp4">
        Your browser does not support the video tag.
    </video>
    """
    return HTML(video_html)

current_video_index = 0

def get_video_path(index):
    return os.path.join(video_folder_path, video_files[index])


    # Function to move to the next video
def next_video():
    global current_video_index
    current_video_index = (current_video_index + 1) % len(video_files)
    display(display_video(get_video_path(current_video_index)))

# Function to move to the previous video
def prev_video():
    global current_video_index
    current_video_index = (current_video_index - 1) % len(video_files)
    display(display_video(get_video_path(current_video_index)))

# Display buttons to control video cycling
from IPython.display import display, Javascript

def create_video_controls():
    display(Javascript('''
    function nextVideo() {
        google.colab.kernel.invokeFunction('notebook.next_video', [], {});
    }

    function prevVideo() {
        google.colab.kernel.invokeFunction('notebook.prev_video', [], {});
    }

    let div = document.createElement('div');
    div.innerHTML = `
        <button onclick="prevVideo()">Previous</button>
        <button onclick="nextVideo()">Next</button>
    `;
    document.body.appendChild(div);
    '''))

create_video_controls()

from google.colab import output

output.register_callback('notebook.next_video', next_video)
output.register_callback('notebook.prev_video', prev_video)

display_video(get_video_path(current_video_index))

<IPython.core.display.Javascript object>

In [ ]:
!pip install opencv-python
!pip install opencv-python-headless


In [ ]:
mp4 = open('/content/clips/NYPD_N_00000592-Scene-001.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)